In [14]:
import polars as pl

In [15]:
out_file = '../datasets/compiled.jsonl'

file = '../datasets/databricks-dolly-15k.jsonl'

df = pl.scan_ndjson(
    file
)


In [4]:
df.head(5).collect()

shape: (5, 4)
┌────────────────────────────┬───────────────────────┬────────────────────────────┬────────────────┐
│ instruction                ┆ context               ┆ response                   ┆ category       │
│ ---                        ┆ ---                   ┆ ---                        ┆ ---            │
│ str                        ┆ str                   ┆ str                        ┆ str            │
╞════════════════════════════╪═══════════════════════╪════════════════════════════╪════════════════╡
│ When did Virgin Australia  ┆ Virgin Australia, the ┆ Virgin Australia commenced ┆ closed_qa      │
│ start …                    ┆ trading na…           ┆ servi…                     ┆                │
│ Which is a species of      ┆                       ┆ Tope                       ┆ classification │
│ fish? Tope…                ┆                       ┆                            ┆                │
│ Why can camels survive for ┆                       ┆ Camels use the fat in      ┆ open_qa        │
│ long …                     ┆                       ┆ their hump…                ┆                │
│ Alice's parents have three ┆                       ┆ The name of the third      ┆ open_qa        │
│ daugh…                     ┆                       ┆ daughter i…                ┆                │
│ When was Tomoaki Komorida  ┆ Komorida was born in  ┆ Tomoaki Komorida was born  ┆ closed_qa      │
│ born?                      ┆ Kumamoto Pr…          ┆ on Jul…                    ┆                │
└────────────────────────────┴───────────────────────┴────────────────────────────┴────────────────┘

In [16]:
unwanted_words = [
    "as a language model",
    "as an AI language model",
    "as an AI",
    "as an AI language",
    "as a large language",
]

filtered = df.filter(
    ~pl.col('response').str.contains('|'.join(unwanted_words))
).collect()

In [22]:
odf = filtered.with_columns(
    pl.lit('databricks-dolly-15k').alias('source'),
    pl.lit('').alias('system'),
    pl.lit('').alias('message'),
    tags = ['instruct', 'synthetic'],
).rename(
    {'instruction': 'input'}
).select(['input', 'response', 'source', 'context', 'system', 'message', 'tags'])


In [23]:
odf.head(5)

shape: (5, 7)
┌───────────────┬───────────────┬───────────────┬───────────────┬────────┬─────────┬───────────────┐
│ input         ┆ response      ┆ source        ┆ context       ┆ system ┆ message ┆ tags          │
│ ---           ┆ ---           ┆ ---           ┆ ---           ┆ ---    ┆ ---     ┆ ---           │
│ str           ┆ str           ┆ str           ┆ str           ┆ str    ┆ str     ┆ list[str]     │
╞═══════════════╪═══════════════╪═══════════════╪═══════════════╪════════╪═════════╪═══════════════╡
│ When did      ┆ Virgin        ┆ databricks-do ┆ Virgin        ┆        ┆         ┆ ["instruct",  │
│ Virgin        ┆ Australia     ┆ lly-15k       ┆ Australia,    ┆        ┆         ┆ "synthetic"]  │
│ Australia     ┆ commenced     ┆               ┆ the trading   ┆        ┆         ┆               │
│ start …       ┆ servi…        ┆               ┆ na…           ┆        ┆         ┆               │
│ Which is a    ┆ Tope          ┆ databricks-do ┆               ┆        ┆         ┆ ["instruct",  │
│ species of    ┆               ┆ lly-15k       ┆               ┆        ┆         ┆ "synthetic"]  │
│ fish? Tope…   ┆               ┆               ┆               ┆        ┆         ┆               │
│ Why can       ┆ Camels use    ┆ databricks-do ┆               ┆        ┆         ┆ ["instruct",  │
│ camels        ┆ the fat in    ┆ lly-15k       ┆               ┆        ┆         ┆ "synthetic"]  │
│ survive for   ┆ their hump…   ┆               ┆               ┆        ┆         ┆               │
│ long …        ┆               ┆               ┆               ┆        ┆         ┆               │
│ Alice's       ┆ The name of   ┆ databricks-do ┆               ┆        ┆         ┆ ["instruct",  │
│ parents have  ┆ the third     ┆ lly-15k       ┆               ┆        ┆         ┆ "synthetic"]  │
│ three daugh…  ┆ daughter i…   ┆               ┆               ┆        ┆         ┆               │
│ When was      ┆ Tomoaki       ┆ databricks-do ┆ Komorida was  ┆        ┆         ┆ ["instruct",  │
│ Tomoaki       ┆ Komorida was  ┆ lly-15k       ┆ born in       ┆        ┆         ┆ "synthetic"]  │
│ Komorida      ┆ born on Jul…  ┆               ┆ Kumamoto Pr…  ┆        ┆         ┆               │
│ born?         ┆               ┆               ┆               ┆        ┆         ┆               │
└───────────────┴───────────────┴───────────────┴───────────────┴────────┴─────────┴───────────────┘

In [24]:

with open(out_file, mode="ab") as f:
    odf.write_ndjson(f)

In [7]:
# show what's filtered and why

filtered = df.filter(
    pl.col('response').str.contains('|'.join(unwanted_words))
).collect()

for row in filtered.select(['response']).rows():
    print(row[0])
    contains = []
    contains = [word for word in unwanted_words if word in row[0]]
    print(f'\n\n\n***Contains:\n{contains}\n')
    
    print('-------------')

Virgin Australia commenced services on 31 August 2000 as Virgin Blue, with two aircraft on a single route.



***Contains:
[]

-------------
Tope



***Contains:
[]

-------------
Camels use the fat in their humps to keep them filled with energy and hydration for long periods of time.



***Contains:
[]

-------------
The name of the third daughter is Alice



***Contains:
[]

-------------
Tomoaki Komorida was born on July 10,1981.



***Contains:
[]

-------------
No. 
Stalemate is a drawn position. It doesn't matter who has captured more pieces or is in a winning position



***Contains:
[]

-------------
Lollapalooze is an annual musical festival held in Grant Park in Chicago, Illinois. It was started in 1991 as a farewell tour by Perry Farrell, singe of the group Jane's Addiction. The festival includes an array of musical genres including alternative rock, heavy metal, punk rock, hip hop, and electronic dance music. The festivals welcomes an estimated 400,000 people each year and 

In [15]:
filtered[0, 2]

'It depends on who you ask, but as an AI language model, I cannot determine which sport is the best. The best sport for a person may differ compared to another person based on the level of athleticism and the complexity of the game required. Some of the popular sports around the world include soccer, basketball, baseball, football, tennis, cricket, and others.'